In [1]:
from functools import cache
import pandas as pd

pd.set_option("display.max_columns", None)

In [2]:
estados_mexicanos = {
    "AGUASCALIENTES",
    "BAJA CALIFORNIA",
    "BAJA CALIFORNIA SUR",
    "CAMPECHE",
    "CHIAPAS",
    "CHIHUAHUA",
    "COAHUILA DE ZARAGOZA",
    "COLIMA",
    "DISTRITO FEDERAL",
    "DURANGO",
    "GUANAJUATO",
    "GUERRERO",
    "HIDALGO",
    "JALISCO",
    "MEXICO",
    "MICHOACAN DE OCAMPO",
    "MORELOS",
    "NAYARIT",
    "NUEVO LEON",
    "OAXACA",
    "PUEBLA",
    "QUERETARO  DE ARTEAGA",
    "QUINTANA ROO",
    "SAN LUIS POTOSI",
    "SINALOA",
    "SONORA",
    "TABASCO",
    "TAMAULIPAS",
    "TLAXCALA",
    "VERACRUZ DE IGNACIO DE LA LLAVE",
    "YUCATAN",
    "ZACATECAS",
}

In [3]:
df = pd.read_csv("2010-2019.csv")

/var/folders/05/y38rqjl55hjb_hbnypxzgrsw0000gn/T/ipykernel_93405/3168623387.py:1: DtypeWarning: Columns (21) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("2010-2019.csv")


In [6]:
def _ano_nacimiento_vivo_func(str_date):
    try:
        return str_date.split("/")[-1]
    except:
        return ""


df["año_de_nacimiento_vivo"] = df["fecha_nacimiento_nac_vivo"].apply(
    _ano_nacimiento_vivo_func
)

In [34]:
df = df[(5 < df["edad_madre"]) & (df["edad_madre"] < 90)]

In [35]:
df_trisomias = df[df["codigo_anomalia"].apply(lambda x: "Q9" in str(x))]

In [36]:
consulta_trisomias = df_trisomias.groupby(
    ["edo_captura", "año_de_nacimiento_vivo"]
).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)
consulta_trisomias

edad_madre                              
                                           count       mean        std min max
edo_captura    año_de_nacimiento_vivo                                         
AGUASCALIENTES 2010                           29  30.586207   9.037688  16  45
               2011                           34  33.823529   6.815626  17  45
               2012                           30  29.600000   8.880820  17  43
               2013                           30  30.400000   9.761289  15  43
               2014                           23  28.956522   7.968565  19  41
...                                          ...        ...        ...  ..  ..
ZACATECAS      2015                           13  31.307692   7.951778  19  43
               2016                            8  29.000000   9.971388  16  45
               2017                            9  32.555556  10.013879  18  43
               2018                           15  33.000000   8.026741  16  41
               2019                           12  26.583333   5.468228  18  35

[320 rows x 5 columns]

In [37]:
# Edades de madres
consulta_total = df.groupby(["edo_captura", "año_de_nacimiento_vivo"]).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)
consulta_total

edad_madre                             
                                           count       mean       std min max
edo_captura    año_de_nacimiento_vivo                                        
AGUASCALIENTES 2010                        26973  25.569792  6.364083  10  52
               2011                        28361  25.576073  6.362188  11  47
               2012                        28840  25.510576  6.370119  12  47
               2013                        28695  25.435302  6.343520  10  53
               2014                        28718  25.434048  6.321484  12  56
...                                          ...        ...       ...  ..  ..
ZACATECAS      2015                        30099  25.619157  6.412798  12  57
               2016                        30118  25.641975  6.402262  10  51
               2017                        29955  25.663896  6.365496  13  53
               2018                        28235  25.756933  6.407207  10  50
               2019                        26800  25.978619  6.402249   9  50

[320 rows x 5 columns]

In [38]:
consulta = consulta_total.join(
    consulta_trisomias, rsuffix="_trisomias", lsuffix="_general"
)

In [39]:
consulta["porcentaje"] = (
    consulta[("edad_madre_trisomias", "count")]
    / consulta[("edad_madre_general", "count")]
)

In [40]:
consulta

edad_madre_general                       \
                                                   count       mean       std   
edo_captura    año_de_nacimiento_vivo                                           
AGUASCALIENTES 2010                                26973  25.569792  6.364083   
               2011                                28361  25.576073  6.362188   
               2012                                28840  25.510576  6.370119   
               2013                                28695  25.435302  6.343520   
               2014                                28718  25.434048  6.321484   
...                                                  ...        ...       ...   
ZACATECAS      2015                                30099  25.619157  6.412798   
               2016                                30118  25.641975  6.402262   
               2017                                29955  25.663896  6.365496   
               2018                                28235  25.756933  6.407207   
               2019                                26800  25.978619  6.402249   

                                              edad_madre_trisomias             \
                                      min max                count       mean   
edo_captura    año_de_nacimiento_vivo                                           
AGUASCALIENTES 2010                    10  52                   29  30.586207   
               2011                    11  47                   34  33.823529   
               2012                    12  47                   30  29.600000   
               2013                    10  53                   30  30.400000   
               2014                    12  56                   23  28.956522   
...                                    ..  ..                  ...        ...   
ZACATECAS      2015                    12  57                   13  31.307692   
               2016                    10  51                    8  29.000000   
               2017                    13  53                    9  32.555556   
               2018                    10  50                   15  33.000000   
               2019                     9  50                   12  26.583333   

                                                         porcentaje  
                                             std min max             
edo_captura    año_de_nacimiento_vivo                                
AGUASCALIENTES 2010                     9.037688  16  45   0.001075  
               2011                     6.815626  17  45   0.001199  
               2012                     8.880820  17  43   0.001040  
               2013                     9.761289  15  43   0.001045  
               2014                     7.968565  19  41   0.000801  
...                                          ...  ..  ..        ...  
ZACATECAS      2015                     7.951778  19  43   0.000432  
               2016                     9.971388  16  45   0.000266  
               2017                    10.013879  18  43   0.000300  
               2018                     8.026741  16  41   0.000531  
               2019                     5.468228  18  35   0.000448  

[320 rows x 11 columns]